# Processo seletivo datarisk
### Notebook do Case - Modelo preditivo para aprovação de crédito

## 1. Introdução


### 1.1 Contexto e descrição do problema do projeto

Modelos de score de crédito calculam a probabilidade de inadimplência e são uma das
principais ferramentas utilizadas por diversas empresas para aprovar ou negar um
crédito.
O objetivo deste desafio é criar um modelo preditivo calculando a probabilidade de
inadimplência de cada novo pedido de crédito.



### 1.2 Descrição do conjunto de dados

Cada linha representa um cliente e as colunas representam os dados (informações) desses
clientes.
A variável resposta é a coluna inadimplente, que indica se o tomador veio a se tornar
inadimplente(1) ou não(0).
As variáveis da base de dados são descritas abaixo:

    - idade: A idade do cliente..
    - numero_de_dependentes: O número de pessoas dependentes do cliente.
    - salario_mensal: Salário mensal do cliente.
    - numero_emprestimos_imobiliarios: Quantidade de empréstimos imobiliários que o cliente possui em aberto.
    - numero_vezes_passou_90_dias: Número de vezes que o tomador passou mais de 90 dias em atraso.
    - util_linhas_inseguras: Quanto que o cliente está usando, relativamente ao limite dele, de linhas de crédito que não são seguradas por qualquer bem do tomador e.g: imoveis, carros etc.
    - vezes_passou_de_30_59_dias: Número de vezes que o cliente atrasou, entre 30 e 59 dias, o pagamento de um empréstimo.
    - razao_debito: Razão entre as dívidas e o patrimônio do tomador. razão débito = Dividas/Patrimônio
    - numero_linhas_crdto_aberto: Número de empréstimos em aberto pelo cliente.
    - numero_de_vezes_que_passou_60_89_dias: Número de vezes que o cliente atrasou, entre 60 e 89 dias, o pagamento de um empréstimo.

Obs: Estes dados foram retirados de terceiros, portanto é possível que existam
incoerências, o que é perfeitamente comum em dados reais.



### 1.3 Visão geral da metodologia

Neste projeto, a metodologia CRISP (Cross-Industry Standard Process) foi adotada para projetos de mineração e análise de dados. A metodologia CRISP é uma estrutura amplamente utilizada que fornece uma abordagem estruturada para orientar um projeto do início ao fim. Ela consiste de seis fases principais, a saber, Compreensão do Negócio, Compreensão de Dados, Preparação de Dados, Modelagem, Avaliação e Implantação.

A metodologia foi escolhida devido à sua natureza cíclica, o que permite a melhoria contínua do projeto. O processo cíclico significa que após a fase de implantação, os resultados do projeto são revisados, e melhorias podem ser feitas em iterações futuras. Além disso, a metodologia proporciona uma abordagem sistemática e rigorosa do projeto de ciência dos dados, assegurando que as metas e objetivos sejam alcançados de forma estruturada e eficiente.

A metodologia foi adaptada para se adequar às necessidades específicas do projeto. Embora a fase de implantação seja uma parte crítica da metodologia CRISP, foi decidido deixá-la fora do escopo deste projeto. Portanto, o foco será nas cinco primeiras fases da metodologia CRISP, que são Compreensão do Negócio, Compreensão de Dados, Preparação de Dados, Modelagem e Avaliação.


### 1.4 Bibliotecas utilizadas

In [1]:
import pandas as pd
import numpy as np
from pycaret.classification import *
import matplotlib.pyplot as plt
from sklearn.model_selection import learning_curve
from sklearn.model_selection import train_test_split
from ydata_profiling import ProfileReport

## 2. Compreensão e exploração dos dados

### 2.1 Carregamento dos dados


In [2]:
treino = pd.read_csv('treino.csv')
teste = pd.read_csv('teste.csv')

### 2.2 Framework de validação


In [11]:
# Importe o módulo e a função necessários
from sklearn.model_selection import train_test_split
# Separe o conjunto de dados em conjuntos de treinamento completo e teste com uma taxa de 0,2 e um estado aleatório de 1
df_full_train, df_test = train_test_split(treino, test_size=0.2, random_state=1)
# Divida ainda mais o conjunto de treinamento completo em conjuntos de treinamento e validação com uma taxa de 0,25 e um estado aleatório de 1
df_train, df_val = train_test_split(df_full_train, test_size=0.25, random_state=1)

# Redefina os índices de todos os dataframes para começar a partir de 0
df_train = df_train.reset_index(drop=True)
df_val = df_val.reset_index(drop=True)
df_test = df_test.reset_index(drop=True)
df_full_train = df_full_train.reset_index(drop=True)

# Print do comprimento dos conjuntos de treinamento, validação e teste
print('Treino:', len(df_train),'Validação:', len(df_val),'Teste:', len(df_test))

# Crie matrizes da coluna "inadimplente" para os conjuntos de treinamento, validação e teste e exclua a coluna "inadimplente" de cada dataframe
y_train = df_train.inadimplente.values
y_val = df_val.inadimplente.values
y_test = df_test.inadimplente.values
del df_train['inadimplente']
del df_val['inadimplente']
del df_test['inadimplente']


Treino: 66000 Validação: 22000 Teste: 22000


### 2.3 Visualização e análise exploratória dos dados


Nesta seção, será realizada uma análise exploratória de dados (EDA) no conjunto de dados de treinamento usando a biblioteca ydata profiling (antigamente chamada pandas profilling) para obter insights e prepará-los para modelagem. Esta ferramenta poderosa gera relatórios detalhados sobre o conjunto de dados, fornecendo uma maneira rápida de entender a distribuição de valores, identificar valores ausentes ou duplicados e destacar problemas potenciais. Ela também nos ajudará a descobrir padrões e tendências importantes que podem orientar decisões de pré-processamento e modelagem, além de fornecer visualizações e estatísticas resumidas para comunicação das descobertas.

In [4]:
profile = ProfileReport(df_full_train, title="Relatório do conjunto de treinamento")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

A análise dos dados revelou que:
 - As classes estão extremamente desbalanceadas (93.7% vs 6.7%);
 - Dois atributos (salario_mensal e numero_de_dependentes) contém valores nulos ou faltantes;
 - Os atributos vezes_passou_de_30_59_dias, numero_vezes_passou_90_dias, numero_de_vezes_que_passou_60_89_dias e numero_de_dependentes são compostos majoritariamente por zeros;
 - Os histogramas revelam que a maioria dos atributos possuem distribuições extremamente assimétricas.

Dessa forma, é necessário, respectivamente:
- Utilizar estratégias de balanceamento dos dados (atribuição de pesos, undersampling ou oversampling) ou então empregar um modelo de identificação de outliers (isolation forest, por exemplo);
- Tratar os valores nulos, imputando novos valores (média, mediana, moda, ou como algoritmo KNN) e/ou excluindo os atributos/exemplos com valores nulos;
- Considerar transformar atributos com muitos zeros em atributos binários (0 ou maior que 0);
- Excluir/modificar outliers, transformar a escala (log, recíproca, box-cox, etc.) ou escalonar os atributos com distribuições assimétricas.

## 3. Seleção e Engenharia de Atributos
- Técnicas de seleção de atributos
- Métodos de engenharia de atributos
- Redução de dimensionalidade


In [5]:
df_train['salario_mensal']

0         1092.0
1            NaN
2         4116.0
3        12500.0
4            NaN
          ...   
65995    17833.0
65996     3500.0
65997     5148.0
65998     9160.0
65999        NaN
Name: salario_mensal, Length: 66000, dtype: float64

## 4. Modelagem
- Escolha e implementação de modelos de aprendizado de máquina
- Treinamento dos modelos
- Ajuste de hiperparâmetros
- Avaliação dos modelos


In [13]:
import optuna
from optuna.samplers import TPESampler
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer, KNNImputer
from imblearn.pipeline import Pipeline as imbPipeline
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler, TomekLinks
from sklearn.preprocessing import RobustScaler
from sklearn.model_selection import cross_val_score
from lightgbm import LGBMClassifier

# Define the pipeline steps for preprocessing and model building
preprocessing = Pipeline([
    #('imputer', SimpleImputer()),
    ('scaler', RobustScaler())
])

models = {
    'LightGBM': LGBMClassifier(),
}

strategies = {
    'mean': SimpleImputer(strategy='mean'),
    'median': SimpleImputer(strategy='median'),
    'knn': KNNImputer()
}

samplers = {
    'undersampling': TomekLinks(),
    'oversampling': SMOTE(),
    'class_weight': 'balanced'
}

# Define the objective function to be minimized by Optuna
def objective(trial):
    # Set up the hyperparameters to optimize
    params = {
        'num_leaves': trial.suggest_int('num_leaves', 10, 1000),
        'learning_rate': trial.suggest_float('learning_rate', 0.001, 0.1),
        'max_depth': trial.suggest_int('max_depth', 2, 20),
        'n_estimators': trial.suggest_int('n_estimators', 10, 1000),
        'min_child_samples': trial.suggest_int('min_child_samples', 5, 100),
        'reg_alpha': trial.suggest_float('reg_alpha', 0, 1),
        'reg_lambda': trial.suggest_float('reg_lambda', 0, 1)
    }

    # Select a random imputation strategy and sampling strategy
    imputation = trial.suggest_categorical('imputation', list(strategies.keys()))
    sampling = trial.suggest_categorical('sampling', list(samplers.keys()))

    # Create the pipeline with the selected imputation and sampling strategies
    if sampling != 'class_weight':
        model = models['LightGBM'].set_params(**params)
        pipeline = Pipeline([
            ('preprocessing', preprocessing),
            ('imputation', strategies[imputation]),
            ('model', model)
        ])
        sampler =  samplers[sampling]
        X, y = sampler.fit_resample(pipeline[1].fit_transform(df_train), y_train)
    else:
        params['class_weight'] = samplers['class_weight']
        model = models['LightGBM'].set_params(**params)
        pipeline = Pipeline([
            ('preprocessing', preprocessing),
            ('imputation', strategies[imputation]),
            ('model', model)
        ])
        X, y = df_train, y_train
    # Evaluate the pipeline with cross-validation and return the mean AUC score
    pipeline.fit(X,y)
    cv_scores = cross_val_score(pipeline, X, y, cv=5, scoring='roc_auc')
    mean_auc = cv_scores.mean()
    return 1.0 - mean_auc

# Run the hyperparameter optimization using Optuna
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=100)

# Print the best hyperparameters found and the corresponding AUC score
best_params = study.best_params
best_score = 1.0 - study.best_value
print(f'Best hyperparameters: {best_params}')
print(f'Best AUC score: {best_score:.4f}')

[I 2023-02-15 16:24:57,532] A new study created in memory with name: no-name-ffe3298e-59a8-4107-a809-90e4a9b5a6f8
[I 2023-02-15 16:25:11,529] Trial 0 finished with value: 0.15965945476722754 and parameters: {'num_leaves': 386, 'learning_rate': 0.09530980288996461, 'max_depth': 6, 'n_estimators': 650, 'min_child_samples': 13, 'reg_alpha': 0.23975190964419502, 'reg_lambda': 0.34074765256158024, 'imputation': 'median', 'sampling': 'undersampling'}. Best is trial 0 with value: 0.15965945476722754.
[I 2023-02-15 16:25:25,409] Trial 1 finished with value: 0.01452370350042076 and parameters: {'num_leaves': 523, 'learning_rate': 0.05439157282965437, 'max_depth': 10, 'n_estimators': 226, 'min_child_samples': 44, 'reg_alpha': 0.5722350776127452, 'reg_lambda': 0.14678461324269443, 'imputation': 'mean', 'sampling': 'oversampling'}. Best is trial 1 with value: 0.01452370350042076.


## 5. Resultados e Avaliação
- Métricas utilizadas para avaliar os modelos
- Comparação do desempenho dos modelos
- Visualização dos resultados dos modelos


## 6. Conclusão
- Resumo das descobertas
- Limitações e áreas para trabalhos futuros
- Conclusão


## 7. Apêndice
- Fragmentos de código ou dados adicionais utilizados no projeto
- Referências
